In [1]:
import pandas as pd

import numpy as np
import os, sys

# pvlib imports
import pvlib

from pvlib.pvsystem import PVSystem

from pvlib.location import Location

from pvlib.modelchain import ModelChain
from pvlib.temperature import TEMPERATURE_MODEL_PARAMETERS


import plotly.express as px
import h5py

In [2]:
def physical_profile(row, df_irr):
    idx, latitude, longitude, tilt, azimuth, capacity = row

    temperature_model_parameters = TEMPERATURE_MODEL_PARAMETERS["sapm"][
        "open_rack_glass_glass"
    ]

    location = Location(latitude=latitude, longitude=longitude)

    pvwatts_system = PVSystem(
        surface_tilt=tilt,
        surface_azimuth=azimuth,
        module_parameters={"pdc0": capacity, "gamma_pdc": -0.004},
        inverter_parameters={"pdc0": capacity},
        temperature_model_parameters=temperature_model_parameters,
    )

    mc = ModelChain(
        pvwatts_system, location, aoi_model="physical", spectral_model="no_loss" #these are my model chain assumptions
    )
    mc.run_model(df_irr)
    results = mc.results.ac

    df_results = pd.Series(results)
    df_results.index = df_results.index.tz_localize(None)
    df_results.index.name = "timestamp"
    df_results.name = idx

    return df_results

In [4]:
timesteplen = 30 # in seconds
limit = int((60/timesteplen) * 15)

target_timesteplen = 5 #minutes

## Load


## Data Extraction Notebook: Hdf5 -> Parquet

* Publication: Schlemminger, M., Ohrdes, T., Schneider, E., & Knoop, M. (2022). Dataset on electrical single-family house and heat pump load profiles in Germany. Scientific Data, 9(1), 1-11.
* Data Download Link: https://zenodo.org/record/5642902#.Yk2o6zVCS70

In [ ]:

resolution = 15 #min depends on your downloads

df_loads = []
df_weathers = []
for year in [2018, 2019, 2020]:

    filename = "../data/hdf5/{0}_data_{1}min.hdf5".format(year, resolution)

    f = h5py.File(filename)

    group_no_pv = f["NO_PV"] #Only regard those profiles that are not mixed with PV generation

    dfs = {}

    for key in group_no_pv.keys():
        
        table = group_no_pv[key]["HOUSEHOLD"]

        table = table["table"][:]
        
        df = pd.DataFrame(table).dropna().set_index("index")[["P_TOT"]]
        df.index = pd.to_datetime(df.index, unit = "s")

        dfs[key] = df

    df_load = pd.concat(list(dfs.values()), axis=1)
    df_load.columns = list(dfs.keys())
    df_load = df_load.fillna(method = "pad").dropna()
    df_loads.append(df_load)

df_load_final = pd.concat(df_loads, axis = 0).sort_index().drop_duplicates()
df_load_total = df_load_final["2019-01-01": "2020-01-01"]
df_load_total_2 = df_load_total.apply(lambda x: x.sub(x.groupby(x.index.date).transform("min")))
df_load_total_2[df_load_total_2<0] = 0

df_load_total_2 = df_load_total_2.drop(labels = ["SFH24"], axis = 1)
df_load_total_2 = df_load_total_2.fillna(method = "bfill", limit = 4).dropna() #bfilling 1 hour of values (for 15 minute resolution)
df_load_total_2.to_csv("../../../Data/Load/load_data_15min_watts.csv")

## PV

### Power Data

In [3]:
df_power = pd.read_csv("/Users/nikolaushouben/Desktop/full_utrecht_pv/filtered_pv_power_measurements_ac.csv")

In [8]:
df_power = df_power.set_index("DateTime")
df_power.index = pd.DatetimeIndex(df_power.index)
df_power = df_power.resample("15T").mean()
df_power.columns = [int(col[-3:]) for col in df_power.columns]
df_power = df_power.tz_localize(None)
test_period_index = pd.date_range("2015-02-15", "2015-03-15", freq="15T")
df_power_period = df_power.reindex(test_period_index)
x = df_power_period.loc[:, (df_power_period.isna().sum(axis = 0) / df_power_period.shape[0]) < 0.1] # coarse filter for systems with enough data points
df_power_filtered = df_power.loc[:,x.columns]



ID001  ID002  ID003  ID004  ID005  ID006  ID007  \
DateTime                                                                     
2014-01-01 00:00:00+00:00    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2014-01-01 00:01:00+00:00    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2014-01-01 00:02:00+00:00    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2014-01-01 00:03:00+00:00    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2014-01-01 00:04:00+00:00    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...                          ...    ...    ...    ...    ...    ...    ...   
2017-12-31 23:54:00+00:00    NaN    NaN    0.0    0.0    0.0    NaN    0.0   
2017-12-31 23:55:00+00:00    NaN    NaN    0.0    0.0    0.0    NaN    0.0   
2017-12-31 23:56:00+00:00    NaN    NaN    0.0    0.0    0.0    NaN    0.0   
2017-12-31 23:57:00+00:00    NaN    NaN    0.0    0.0    0.0    NaN    0.0   
2017-12-31 23:58:00+00:00    NaN    NaN    0.0    0.0    0.0    NaN    0.0   

                           ID008  ID009  ID010  ...  ID166  ID167  ID168  \
DateTime                                        ...                        
2014-01-01 00:00:00+00:00    0.0    0.0    0.0  ...    NaN    NaN    NaN   
2014-01-01 00:01:00+00:00    0.0    0.0    0.0  ...    NaN    NaN    NaN   
2014-01-01 00:02:00+00:00    0.0    0.0    0.0  ...    NaN    NaN    NaN   
2014-01-01 00:03:00+00:00    0.0    0.0    0.0  ...    NaN    NaN    NaN   
2014-01-01 00:04:00+00:00    0.0    0.0    0.0  ...    NaN    NaN    NaN   
...                          ...    ...    ...  ...    ...    ...    ...   
2017-12-31 23:54:00+00:00    NaN    0.0    0.0  ...    NaN    NaN    0.0   
2017-12-31 23:55:00+00:00    NaN    0.0    0.0  ...    NaN    NaN    0.0   
2017-12-31 23:56:00+00:00    NaN    0.0    0.0  ...    NaN    NaN    0.0   
2017-12-31 23:57:00+00:00    NaN    0.0    0.0  ...    NaN    NaN    0.0   
2017-12-31 23:58:00+00:00    NaN    0.0    0.0  ...    NaN    NaN    0.0   

                           ID169  ID170  ID171  ID172  ID173  ID174  ID175  
DateTime                                                                    
2014-01-01 00:00:00+00:00    NaN    NaN    NaN    NaN    NaN    0.0    0.0  
2014-01-01 00:01:00+00:00    NaN    NaN    NaN    NaN    NaN    0.0    0.0  
2014-01-01 00:02:00+00:00    NaN    NaN    NaN    NaN    NaN    0.0    0.0  
2014-01-01 00:03:00+00:00    NaN    NaN    NaN    NaN    NaN    0.0    0.0  
2014-01-01 00:04:00+00:00    NaN    NaN    NaN    NaN    NaN    0.0    0.0  
...                          ...    ...    ...    ...    ...    ...    ...  
2017-12-31 23:54:00+00:00    NaN    0.0    NaN    NaN    0.0    NaN    NaN  
2017-12-31 23:55:00+00:00    NaN    0.0    NaN    NaN    0.0    NaN    NaN  
2017-12-31 23:56:00+00:00    NaN    0.0    NaN    NaN    0.0    NaN    NaN  
2017-12-31 23:57:00+00:00    NaN    0.0    NaN    NaN    0.0    NaN    NaN  
2017-12-31 23:58:00+00:00    NaN    0.0    NaN    NaN    0.0    NaN    NaN  

[2103839 rows x 175 columns]

### Meta Data

Filtering the Meta Dataset to only include the systems we have selected in the previous step

In [57]:
df_meta_data_full = pd.read_csv("/Users/nikolaushouben/Desktop/full_utrecht_pv/metadata complete.csv", sep = ";")
idx = df_meta_data_full.ID.apply(lambda x: int(x[-3:]))
df_meta_data_full.index = idx
df_meta_data_full["ID"] = df_meta_data_full.ID.apply(lambda x: int(x[-3:]))
df_meta_data_full = df_meta_data_full[["ID", "latitude", "longitude", "tilt", "azimuth", "estimated_dc_capacity"]]
df_meta_data_filtered = df_meta_data_full.loc[x.columns,:].astype("float32")
df_meta_data_filtered.to_csv("../../../Input_Data/PV_Meta_Data_All.csv")

### PV Power Data Imputation with Physical Model Chain

In [ ]:
df_irr = pd.read_csv("../../../Input_Data/ghi_dni_dhi.csv", index_col=0, parse_dates=True).resample("15T").mean() # more complete than the other one
df_irr = df_irr[['ghi', 'dni', 'dhi']]

In [84]:
list_of_df_physicals = [physical_profile(df_meta_data_filtered.iloc[row_idx], df_irr) for row_idx in range(df_meta_data_filtered.shape[0])]
df_phys = pd.concat(list_of_df_physicals, axis = 1)
df_phys.columns = [int(col) for col in df_phys.columns]
df_power_filled = df_power_filtered.reindex(df_phys.index).fillna(df_phys)

In [115]:
df_power_filled.to_csv("../../../Input_Data/UTC_PV_Power_Data_All.csv")

## Net Load

In [57]:
df_load = pd.read_csv("../../../Data/Load/load_data_15min_watts.csv", parse_dates=True, index_col=0).resample("15T").mean()
df_load_agg = df_load.sum(axis = 1).to_frame("total_load")
df_load = df_load.tshift(-365* 4, freq = "D")

/var/folders/35/267ql_w95qlgmrzwgprns44w0000gn/T/ipykernel_52975/1371532820.py:3: FutureWarning:

tshift is deprecated and will be removed in a future version. Please use shift instead.



In [58]:
df_pv = pd.read_csv("../../../Data/PV/UTC_PV_Power_Data_All.csv", index_col=0, parse_dates=True)

In [73]:
np.random.seed(42)


def weighted_average(df, n_columns=3):
    # Randomly select n_columns from the DataFrame
    columns = np.random.choice(df.columns, n_columns, replace=False)

    print(columns)
    # Generate random weights for the selected columns
    weights = np.random.rand(n_columns)
    
    # Define a function that calculates the weighted average for each row
    def _weighted_average(row):
        return np.average([row[col] for col in columns], weights=weights)
    
    # Apply the function to each row of the DataFrame
    df_load_av = df.apply(_weighted_average, axis=1).to_frame("load")
    
    
    return df_load_av

In [74]:

list_df_sfh = []
for pv_column in df_pv:
    df_pv_sfh = df_pv[[pv_column]]
    df_load_sfh = weighted_average(df_load, 5)
    df_load_sfh.columns = [df_load_sfh.columns[0] + "_" + df_pv_sfh.columns[0]]
    df_sfh = pd.merge(df_pv_sfh, df_load_sfh, left_index=True, right_index=True)
    df_sfh["net_load_{}".format(df_pv_sfh.columns[0])] = df_sfh.iloc[:,1] - df_sfh.iloc[:,0]
    list_df_sfh.append(df_sfh)


['SFH4' 'SFH27' 'SFH38' 'SFH35' 'SFH29']
['SFH29' 'SFH3' 'SFH16' 'SFH21' 'SFH5']
['SFH14' 'SFH11' 'SFH16' 'SFH17' 'SFH4']
['SFH17' 'SFH11' 'SFH3' 'SFH29' 'SFH9']
['SFH27' 'SFH11' 'SFH34' 'SFH14' 'SFH7']
['SFH6' 'SFH28' 'SFH21' 'SFH18' 'SFH29']
['SFH7' 'SFH17' 'SFH31' 'SFH25' 'SFH14']
['SFH25' 'SFH34' 'SFH40' 'SFH21' 'SFH16']
['SFH39' 'SFH35' 'SFH9' 'SFH25' 'SFH18']
['SFH16' 'SFH22' 'SFH4' 'load' 'SFH36']
['SFH37' 'SFH40' 'SFH42' 'SFH18' 'SFH38']
['load' 'SFH19' 'SFH20' 'SFH38' 'SFH36']
['SFH17' 'SFH32' 'SFH4' 'SFH6' 'SFH29']
['SFH22' 'SFH21' 'SFH10' 'SFH19' 'SFH17']
['SFH35' 'SFH31' 'SFH10' 'SFH14' 'SFH8']
['SFH34' 'SFH11' 'SFH27' 'SFH14' 'SFH6']
['SFH9' 'SFH25' 'SFH11' 'SFH4' 'SFH18']
['SFH14' 'SFH19' 'SFH32' 'SFH37' 'SFH31']
['SFH32' 'SFH21' 'SFH20' 'SFH31' 'SFH6']
['SFH40' 'SFH39' 'SFH36' 'load' 'SFH27']
['SFH36' 'SFH30' 'SFH9' 'SFH18' 'SFH38']
['SFH22' 'SFH5' 'SFH6' 'SFH32' 'SFH29']
['SFH27' 'load' 'SFH18' 'SFH5' 'SFH39']
['SFH20' 'load' 'SFH6' 'SFH7' 'SFH34']
['SFH30' 'SFH28' 'SFH

In [52]:
px.line(list_df_sfh[0])

In [82]:
df_all = pd.concat(list_df_sfh, axis = 1)


df_all.to_csv("../../../Data/Net_Load/UTC_netload.csv")

In [81]:
os.getcwd()

'/Users/nikolaushouben/Library/Mobile Documents/com~apple~CloudDocs/PhD_Icloud/PhD_Papers/Paper_2_Collaborative Forecasting/Code/Collaborative_PV_Forecasting/notebooks'

In [85]:
df_net_loads = df_all.filter(like = "net").sum(axis = 1).to_frame("netload_total")

